In [1]:
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
from pytorch_tabnet.tab_model import TabNetClassifier
#from pytorch_tabnet.tab_model import TabNetModel
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
import lightgbm as lgb
import statsmodels.api as sm
import warnings
import shap
import optuna
import torch
from sklearn import svm
import tensorflow as tf
from tensorflow import feature_column
from tensorflow.keras import layers
from tqdm.auto import tqdm
from pytorch_tabnet.tab_model import TabNetRegressor
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_validate
from sklearn.ensemble import VotingClassifier
from sklearn.ensemble import VotingRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import RobustScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import StratifiedKFold
from pycaret.regression import *
from xgboost import XGBRegressor
from xgboost import XGBClassifier
from sklearn.tree import ExtraTreeClassifier
from sklearn.tree import ExtraTreeRegressor
from sklearn.experimental import enable_iterative_imputer 
from sklearn.impute import KNNImputer
from sklearn.impute import IterativeImputer
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostClassifier, Pool
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import AdaBoostRegressor
from catboost import CatBoostRegressor
from catboost import CatBoostClassifier
from sklearn.metrics import mean_squared_error
from sklearn.impute import KNNImputer
from sklearn.decomposition import PCA

In [2]:
warnings.simplefilter(action='ignore')
pd.set_option('display.max_columns', None)

In [3]:
train_data = pd.read_csv("./train.csv")

In [4]:
train_data['YEAR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.year
train_data['MONTH'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.month
train_data['DAY'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day
train_data['HOUR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.hour
train_data['MINUTE'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.minute
train_data['DAY_OF_WEEK'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day_name()

train_data = train_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE', 'HOUR'], axis = 1)

In [5]:
colls = []
for coll in train_data :
    if 'X' in coll and train_data[coll].isna().sum() == 598 :
        colls.append(coll)
print(len(colls))

train_data.drop(colls, inplace = True, axis = 1)

82


In [6]:
train_data.loc[train_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
train_data.loc[train_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
train_data.loc[train_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

train_data.loc[train_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
train_data.loc[train_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
train_data.loc[train_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
train_data.loc[train_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
train_data.loc[train_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
train_data.loc[train_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
train_data.loc[train_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

train_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
train_data

Y_Class  Y_Quality     LINE PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  \
0          1   0.533433  T050304            1   NaN   NaN  NaN   NaN   NaN   
1          2   0.541819  T050307            1   NaN   NaN  NaN   NaN   NaN   
2          1   0.531267  T050304            1   NaN   NaN  NaN   NaN   NaN   
3          2   0.537325  T050307            1   NaN   NaN  NaN   NaN   NaN   
4          1   0.531590  T050304            1   NaN   NaN  NaN   NaN   NaN   
..       ...        ...      ...          ...   ...   ...  ...   ...   ...   
593        1   0.526546  T100306            2   2.0  95.0  0.0  45.0  10.0   
594        0   0.524022  T050304            1   NaN   NaN  NaN   NaN   NaN   
595        0   0.521289  T050304            1   NaN   NaN  NaN   NaN   NaN   
596        1   0.531375  T100304            3  40.0  94.0  0.0  45.0  11.0   
597        1   0.533702  T100306            3  21.0  87.0  0.0  45.0  10.0   

     X_6   X_7   X_8   X_9  X_10   X_11   X_12   X_13  X_14  X_15   X_16  \
0    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
1    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
2    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
3    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
4    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
..   ...   ...   ...   ...   ...    ...    ...    ...   ...   ...    ...   
593  0.0  50.0  10.0  52.0   2.0  468.9  473.9  459.2   0.0   0.0  247.5   
594  NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
595  NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
596  0.0  45.0  10.0  31.0   2.0  505.8  510.9  497.1   0.0   0.0  247.5   
597  0.0  61.0  10.0  52.0   2.0  470.6  474.9  462.9   0.0   0.0  247.5   

      X_17   X_18   X_19   X_20   X_21   X_22  X_23  X_24  X_25   X_26   X_27  \
0      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
..     ...    ...    ...    ...    ...    ...   ...   ...   ...    ...    ...   
593  248.0  247.3  250.0  527.0  538.0  522.0  0.19  0.19  0.19  155.0  155.0   
594    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
596  248.1  247.3  250.0  489.0  498.0  485.0  0.19  0.19  0.19  155.0  155.0   
597  248.0  247.3  250.0  525.0  534.0  520.0  0.19  0.20  0.19  155.0  155.0   

      X_28   X_29   X_30   X_31   X_32   X_33   X_34   X_35   X_36   X_37  \
0      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
593  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   
594    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
596  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   
597  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   

      X_38  X_39  X_40  X_41  X_42  X_43  X_44  X_45  X_46  X_47  X_48  X_49  \
0      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2      NaN   NaN 

In [7]:
T050304 = train_data[train_data['LINE'] == 'T050304']
T050307 = train_data[train_data['LINE'] == 'T050307']
T010305 = train_data[train_data['LINE'] == 'T010305']
T010306 = train_data[train_data['LINE'] == 'T010306']
T100304 = train_data[train_data['LINE'] == 'T100304']
T100306 = train_data[train_data['LINE'] == 'T100306']

T050304.drop(['LINE'], axis = 1, inplace = True)
T050307.drop(['LINE'], axis = 1, inplace = True)
T010305.drop(['LINE'], axis = 1, inplace = True)
T010306.drop(['LINE'], axis = 1, inplace = True)
T100304.drop(['LINE'], axis = 1, inplace = True)
T100306.drop(['LINE'], axis = 1, inplace = True)

In [8]:
T050304_col = []
for col in T050304 :
    if 'X' in col and T050304[col].isna().sum() == len(T050304) :
        T050304_col.append(col)
print(len(T050304_col))

T050307_col = []
for col in T050307 :
    if 'X' in col and T050307[col].isna().sum() == len(T050307) :
        T050307_col.append(col)
print(len(T050307_col))

T010305_col = []
for col in T010305 :
    if 'X' in col and T010305[col].isna().sum() == len(T010305) :
        T010305_col.append(col)
print(len(T010305_col))

T010306_col = []
for col in T010306 :
    if 'X' in col and T010306[col].isna().sum() == len(T010306) :
        T010306_col.append(col)
print(len(T010306_col))

T100304_col = []
for col in T100304 :
    if 'X' in col and T100304[col].isna().sum() == len(T100304) :
        T100304_col.append(col)
print(len(T100304_col))

T100306_col = []
for col in T100306 :
    if 'X' in col and T100306[col].isna().sum() == len(T100306) :
        T100306_col.append(col)
print(len(T100306_col))

825
818
1907
1907
2122
2122


In [9]:
T050304.drop(T050304_col, inplace = True, axis = 1)
T050307.drop(T050307_col, inplace = True, axis = 1)
T010305.drop(T010305_col, inplace = True, axis = 1)
T010306.drop(T010306_col, inplace = True, axis = 1)
T100304.drop(T100304_col, inplace = True, axis = 1)
T100306.drop(T100306_col, inplace = True, axis = 1)

In [10]:
T051 = list(set(T050307_col)-set(T050304_col))
T052 = list(set(T050304_col)-set(T050307_col))
T5drop = T051 + T052

T011 = list(set(T010305_col)-set(T010306_col))
T012 = list(set(T010306_col)-set(T010305_col))
T0drop = T011 + T012

T101 = list(set(T100304_col)-set(T100306_col))
T102 = list(set(T100306_col)-set(T100304_col))
T1drop = T101 + T102

In [11]:
T05 = pd.concat([T050304, T050307])
T01 = pd.concat([T010305, T010306])
T10 = pd.concat([T100304, T100306])

T05.drop(T5drop, inplace = True, axis = 1)
T01.drop(T0drop, inplace = True, axis = 1)
T10.drop(T1drop, inplace = True, axis = 1)

#T05 = T05.fillna(T05.mean())
#T01 = T01.fillna(T01.mean())
#T10 = T10.fillna(T10.mean())

T05 = T05.fillna(0)
T01 = T01.fillna(0)
T10 = T10.fillna(0)

In [12]:
T05_cols = []
for col in T05 :
    if 'X' in col and T05[col].std() == 0 :
        T05_cols.append(col)
print(len(T05_cols))

T01_cols = []
for col in T01 :
    if 'X' in col and T01[col].std() == 0 :
        T01_cols.append(col)
print(len(T01_cols))

T10_cols = []
for col in T10 :
    if 'X' in col and T10[col].std() == 0 :
        T10_cols.append(col)
print(len(T10_cols))

212
147
116


In [13]:
T05.drop(T05_cols, inplace = True, axis = 1)
T01.drop(T01_cols, inplace = True, axis = 1)
T10.drop(T10_cols, inplace = True, axis = 1)

In [14]:
T05_class = T05['Y_Class']
T05_target = T05['Y_Quality']
T05_data = T05.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [15]:
T_05c = T05_data.columns
T_05scaler = RobustScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)

T05_y_class = pd.DataFrame(T05_target, columns = ['Y_Quality'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_data = pd.concat([T05_data, T05_y_class], axis = 1)
T05_data = T05_data.set_index('index')
T05_data.drop(['Y_Quality'], axis = 1, inplace = True)
T05_data

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
index                                                                           
0               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
2               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
4               0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
6               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
8               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
...             ...    ...    ...    ...    ...       ...       ...       ...   
549             0.0   -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292   
550             0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
551             0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
552             0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
555             0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   

          X_139     X_140     X_141  X_143  X_144  X_145     X_146     X_148  \
index                                                                          
0     -0.024793 -0.052154  0.023438    0.0   -1.0    0.0 -0.003454  0.000000   
2      0.024793 -0.029478  0.315104    0.0    0.0    0.0  0.563040 -0.074074   
4     -0.008264 -0.043084 -0.049479    0.0   -1.0    0.0 -0.348877  0.000000   
6      0.002755 -0.043084 -1.195312    0.0   -2.0    0.0 -4.113990  0.000000   
8     -0.002755 -0.047619  0.263021    0.0    0.0    0.0  0.514680  0.000000   
...         ...       ...       ...    ...    ...    ...       ...       ...   
549   -1.049587 -0.882086 -0.898437    0.0    0.0    0.0  0.373057  1.037037   
550   -1.049587 -0.891156 -0.929687    0.0   -1.0    0.0  0.158895  1.037037   
551   -1.044077 -0.886621 -0.695312    0.0    0.0    0.0  0.618307  1.037037   
552   -1.033058 -0.877551 -0.919271    0.0    0.0    0.0  0.158895  1.037037   
555   -1.082645 -0.877551 -1.263021    0.0   -1.0    0.0 -0.873921  1.111111   

          X_149   X_150  X_151  X_152  X_153  X_155  X_156  X_157  X_159  \
index                                                                      
0      0.072727  0.0625   -1.0    0.0    0.0    0.0    0.0    0.0   -1.0   
2      0.000000  0.0000   -1.0    0.0   -1.0    0.0    0.0    0.0    0.0   
4      0.000000  0.0625    0.0    0.0   -1.0    0.0    0.1    0.1   -1.0   
6      0.000000  0.0000    0.0    0.1    0.0   -1.0    0.0    0.0    0.0   
8      0.000000  0.0625    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...         ...     ...    ...    ...    ...    ...    ...    ...    ...   
549    1.163636  0.8750   -1.0    0.0   -2.0    0.0    0.0    0.0   -1.0   
550    1.163636  0.8750    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
551    1.163636  0.8750   -1.0    0.0   -1.0   -1.0    0.0    0.0   -1.0   
552    1.163636  0.8750   -1.0   -0.1   -1.0    0.0    0.0   -0.1   -1.0   
555    1.236364  0.8750    0.0    0.0    0.0   -1.0    0.0    0.0    0.0   

       X_160  X_161  X_163  X_164  X_165  X_167  X_168  X_169  X_171  X_172  \
index                                                                         
0        0.0    0.0   -0.1    0.0   -0.5   -1.0    0.0    0.0    0.0    0.0   
2        0.0    0.0   -0.1    0.0   -0.5   -1.0    0.0    0.0   -1.0    0.0   
4        0.0    0.0    0.0    1.0    0.5   -1.0    0.0    0.0   -1.0    0.0   
6        0.0    0.0    0.0    0.0   -0.5    0.0    0.0    0.0   -1.0    0.0   
8        0.0    0.0    0.0    1.0    0.5    0.0    0.0    0.0    0.0    0.0   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
549      0.0    0.0   -0.1    0.0   -0.5    0.0    0.0    0.0    0.0    0.0   
550      0.0    0.0    0.0    1.0    0.5    0.0    0.0    0.0   -1.0    0.0   
551      0.0    0.0    0.0    0.0    0.5    0.0    0.1    0.0    0.0    0.0   
552      0.1    0.0   -0.1    0.0   -0.5    0.0    0.0

In [16]:
T01_class = T01['Y_Class']
T01_target = T01['Y_Quality']
T01_data = T01.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [17]:
T_01c = T01_data.columns
T_01scaler = RobustScaler()
T_01scaled = T_01scaler.fit_transform(T01_data)
T01_data = pd.DataFrame(T_01scaled, columns = T_01c)

T01_y_class = pd.DataFrame(T01_target, columns = ['Y_Quality'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_data = pd.concat([T01_data, T01_y_class], axis = 1)
T01_data = T01_data.set_index('index')
T01_data.drop(['Y_Quality'], axis = 1, inplace = True)
T01_data

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_251  X_253  X_254  \
index                                                                        
28              0.0    0.0  -0.25 -0.054348    0.0  1.011236   -1.0   -1.0   
33              0.0    0.0   1.25 -0.054348    0.0  1.101124   -1.0   -1.0   
39              0.0    0.0   1.25 -0.054348    0.0  1.146067    0.0   -1.0   
40              0.0    0.0   1.25 -0.054348    0.0  1.179775   -1.0   -1.0   
41              0.0    0.0  -0.75 -0.054348    0.0  1.179775   -1.0   -1.0   
...             ...    ...    ...       ...    ...       ...    ...    ...   
479             0.0    0.0   0.75  1.108696    0.0  0.000000    0.0    0.0   
501             0.0    1.0   1.25  1.293478    0.0  0.000000    0.0    0.0   
523             0.0    0.0  -0.25  1.423913    1.0  0.000000    0.0    0.0   
531             0.0    0.0   0.00  1.489130    0.0  0.000000    0.0    0.0   
585             0.0    0.0   0.75  0.630435    1.0  0.000000    0.0    0.0   

          X_256     X_257     X_258     X_261  X_262  X_263     X_265  \
index                                                                   
28    -0.145455 -0.198381 -0.068571 -0.333333  -0.75 -0.250  0.095238   
33    -0.131818 -0.137652 -0.125714 -0.666667  -1.00  0.000  0.047619   
39    -0.072727 -0.097166 -0.085714 -0.666667  -1.50 -0.250  0.000000   
40     0.031818  0.000000  0.000000  0.666667   0.25  0.250 -0.095238   
41     0.027273  0.000000  0.057143  0.666667   0.00  0.625 -0.095238   
...         ...       ...       ...       ...    ...    ...       ...   
479    0.068182  0.048583  0.154286 -1.000000   0.25 -1.000 -0.047619   
501    0.295455  0.246964  0.462857 -1.000000  -0.25 -0.500 -0.285714   
523    0.459091  0.421053  0.657143 -1.000000   0.25 -0.875 -0.476190   
531    0.568182  0.481781  0.697143  0.000000   0.75 -0.625 -0.523810   
585   -0.172727 -0.234818  0.000000 -2.000000  -0.50 -1.000  0.190476   

          X_266     X_267  X_268  X_269  X_270  X_271  X_272  X_273  X_275  \
index                                                                        
28     0.105263  0.125000    0.0    0.0    0.0    1.0    0.0    1.0    0.0   
33     0.105263  0.083333    0.0    0.0    0.0    0.0    0.0    0.0    1.0   
39     0.105263 -0.041667    0.0    0.0    0.0    0.0    0.0    0.0    1.0   
40    -0.052632 -0.083333    0.0    0.0    0.0    0.0    0.0    0.0    1.0   
41     0.000000 -0.083333    0.0    0.0    0.0    0.0    0.0    0.0    1.0   
...         ...       ...    ...    ...    ...    ...    ...    ...    ...   
479    0.000000 -0.041667   -1.0    0.0   -1.0    0.0   -1.0    0.0    0.0   
501   -0.210526 -0.291667   -1.0    0.0   -1.0    0.0    0.0    0.0    1.0   
523   -0.368421 -0.458333    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
531   -0.526316 -0.541667   -1.0    0.0   -1.0    0.0    0.0    0.0    1.0   
585    0.210526  0.208333   -1.0    0.0   -1.0    0.0    0.0    0.0    0.0   

       X_276  X_277  X_279  X_280  X_281  X_283  X_285  X_286     X_287  \
index                                                                     
28       0.0    0.0    0.0    0.0    0.0    0.0    0.6    0.4  0.600000   
33       0.0    1.0    0.0    0.0    0.0    0.0    0.6    0.4  0.600000   
39       0.0    1.0    0.0    0.0    0.0   -0.5    0.6    0.4  0.600000   
40       0.0    1.0    0.0    0.0    0.0    0.0    0.6    0.4  0.600000   
41       0.0    1.0    1.0    0.0    1.0    0.5    0.6    0.4  0.600000   
...      ...    ...    ...    ...    ...    ...    ...    ...       ...   
479      0.0    0.0    0.0    0.0    0.0    0.5    0.5    1.1  0.266667   
501      0.0    1.0    0.0    0.0    0.0    1.5    0.5    1.1  0.266667   
523      0.0    0.0    0.0    0.0    0.0    0.0    0.5    1.1  0.266667   
531      0.0    1.0    0.0    0.0    0.0    0.0   -0.2    0.8 -0.066667   
585      0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.9  0.000000   

          X_288     X_289  X_290     X_291     X_29

In [18]:
T10_class = T10['Y_Class']
T10_target = T10['Y_Quality']
T10_data = T10.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [19]:
T_10c = T10_data.columns
T_10scaler = RobustScaler()
T_10scaled = T_10scaler.fit_transform(T10_data)
T10_data = pd.DataFrame(T_10scaled, columns = T_10c)

T10_y_class = pd.DataFrame(T10_target, columns = ['Y_Quality'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_data = pd.concat([T10_data, T10_y_class], axis = 1)
T10_data = T10_data.set_index('index')
T10_data.drop(['Y_Quality'], axis = 1, inplace = True)
T10_data

PRODUCT_CODE   X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12  \
index                                                                         
22              0.0   0.0  1.4  1.0  0.000000  0.0  0.0  0.653153  0.746725   
23              0.0   0.0  1.4  1.0  0.000000  0.0  0.0  0.662162  0.768559   
25              0.0   0.0  0.4  1.0  0.000000  0.0  0.0  0.788288  0.917031   
29              0.0   0.0  1.0  1.0  0.000000  0.0  0.0  0.747748  0.917031   
37              0.0   0.0  1.0  1.0  0.000000  0.0  0.0  0.792793  0.947598   
...             ...   ...  ...  ...       ...  ...  ...       ...       ...   
589             0.0  -1.0 -0.2  0.0  0.833333  0.0  1.0 -1.549550 -1.519651   
590             0.0  -1.0 -1.2  0.0  0.833333  0.0  1.0 -1.527027 -1.506550   
591             0.0  -1.0 -1.6  0.0  0.833333  0.0  1.0 -1.531532 -1.506550   
593             0.0   0.0  0.0  0.0  0.833333  0.0  1.0 -1.396396 -1.358079   
597             1.0  19.0 -1.6  0.0  2.666667  0.0  1.0 -1.319820 -1.314410   

           X_13  X_15  X_16  X_17  X_18      X_20      X_21      X_22  X_23  \
index                                                                         
22     0.714286   0.0   0.0  -1.0  -1.0 -0.636364 -0.652174 -0.727273   0.0   
23     0.723214   0.0   1.0   0.0   1.0 -0.636364 -0.695652 -0.727273   0.0   
25     0.852679   0.0   0.0  -3.0   0.0 -0.772727 -0.826087 -0.909091   0.0   
29     0.790179   0.0   1.0   0.0   1.0 -0.727273 -0.739130 -0.863636   0.0   
37     0.830357   0.0   0.0   0.0  -1.0 -0.772727 -0.826087 -0.909091   0.0   
...         ...   ...   ...   ...   ...       ...       ...       ...   ...   
589   -1.504464   0.0   0.0  -1.0   0.0  1.636364  1.565217  1.636364   0.0   
590   -1.419643   0.0   0.0  -1.0   0.0  1.590909  1.521739  1.636364   0.0   
591   -1.473214   0.0   1.0  -1.0  -1.0  1.590909  1.608696  1.636364   0.0   
593   -1.366071   0.0   0.0  -1.0   0.0  1.454545  1.434783  1.454545   0.0   
597   -1.200893   0.0   0.0  -1.0   0.0  1.363636  1.260870  1.363636   0.0   

       X_24  X_25      X_38  X_39      X_40      X_41      X_42      X_43  \
index                                                                       
22     0.00   0.0  0.333333   0.0  0.000000 -0.185185 -0.473684  0.722222   
23     0.00   0.0  0.333333   0.0  0.000000 -0.185185 -0.473684  0.722222   
25     0.01   0.0  0.333333   0.0 -0.230769 -0.370370 -0.210526  0.444444   
29     0.00   0.0  0.333333   0.0 -0.230769 -0.370370 -0.210526  0.444444   
37     0.00   0.0  0.333333   0.0 -0.230769 -0.370370 -0.210526  0.444444   
...     ...   ...       ...   ...       ...       ...       ...       ...   
589    0.00   0.0 -1.000000   0.0  1.346154  1.407407  1.000000  1.388889   
590    0.00   0.0 -0.666667   0.0  1.346154  1.407407  1.000000  1.388889   
591    0.00   0.0 -1.000000   0.0  1.346154  1.407407  1.000000  1.388889   
593    0.00   0.0 -1.000000   0.0  1.346154  1.407407  1.000000  1.388889   
597    0.01   0.0 -0.333333  -1.0  1.346154  1.407407  1.000000  1.388889   

           X_44  X_45      X_46      X_47      X_48      X_49      X_50  \
index                                                                     
22     0.000000   0.6 -0.125000  0.000000 -0.121212  0.000000 -0.054054   
23     0.000000   0.6 -0.125000  0.000000 -0.121212  0.000000 -0.054054   
25    -0.205882  -0.4 -0.166667 -0.222222 -0.151515  0.275862  0.000000   
29    -0.205882  -0.4 -0.166667 -0.222222 -0.151515  0.275862  0.000000   
37    -0.205882  -0.4 -0.166667 -0.222222 -0.151515  0.275862  0.000000   
...         ...   ...       ...       ...       ...       ...       ...   
589    0.558824  -2.8  0.208333  0.638889  0.515152 -0.137931  0.621622   
590    0.558824  -2.8  0.208333  0.638889  0.515152 -0.137931  0.621622   
591    0.558824  -2.8  0.208333  0.638889  0.515152 -0.137931  0.621622   
593    0.558824  -2.8  0.208333  0.638889  0.515152 -0.137931  0.621622   
597    0.558824  -2.8  0.208333  0.638889  0.5151

In [20]:
T05_data = T05_data.to_numpy()
T01_data = T01_data.to_numpy()
T10_data = T10_data.to_numpy()

T05_class = T05['Y_Class'].to_numpy()
T01_class = T01['Y_Class'].to_numpy()
T10_class = T10['Y_Class'].to_numpy()

# Test

In [21]:
test_data = pd.read_csv("./test.csv")

In [22]:
test_data['YEAR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.year
test_data['MONTH'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.month
test_data['DAY'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day
test_data['HOUR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.hour
test_data['MINUTE'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.minute
test_data['DAY_OF_WEEK'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day_name()

test_data = test_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE', 'HOUR'], axis = 1)

In [23]:
test_data.drop(colls, inplace = True, axis = 1)

In [24]:
test_data.loc[test_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
test_data.loc[test_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
test_data.loc[test_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
test_data.loc[test_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
test_data.loc[test_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
test_data.loc[test_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
test_data.loc[test_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

test_data.loc[test_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
test_data.loc[test_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
test_data.loc[test_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

test_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
test_data

LINE PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  \
0    T100306            2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   
1    T100304            2  2.0  93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   
2    T100304            2  2.0  95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   
3    T010305            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   
4    T010306            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   
..       ...          ...  ...   ...  ...   ...   ...  ...   ...   ...   ...   
305  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   
306  T100304            2  2.0  96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   
307  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   
308  T100306            2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   
309  T100306            2  2.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   

     X_10   X_11   X_12   X_13  X_14  X_15   X_16   X_17   X_18   X_19   X_20  \
0     2.0  469.6  474.4  461.0   0.0   0.0  247.5  248.0  247.2  250.0  526.0   
1     2.0  506.6  511.1  500.1   0.0   0.0  247.6  248.2  247.4  250.0  489.0   
2     2.0  506.6  511.4  500.6   0.0   0.0  247.6  247.9  247.4  250.0  488.0   
3     NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN   
4     NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN   
..    ...    ...    ...    ...   ...   ...    ...    ...    ...    ...    ...   
305   2.0  502.5  511.9  488.3   0.0   0.0  247.5  248.1  247.3  250.0  492.0   
306   2.0  513.7  518.9  505.0   0.0   0.0  247.5  248.1  247.4  250.0  481.0   
307   2.0  502.8  511.6  489.8   0.0   0.0  247.6  248.0  247.3  250.0  491.0   
308   2.0  503.2  512.6  489.8   0.0   0.0  247.5  248.0  247.3  250.0  491.0   
309   2.0  503.3  512.1  489.5   0.0   0.0  247.5  248.0  247.3  250.0  491.0   

      X_21   X_22  X_23  X_24  X_25   X_26   X_27   X_28   X_29   X_30   X_31  \
0    537.0  521.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
1    496.0  484.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
2    496.0  484.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
3      NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN   
4      NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN   
..     ...    ...   ...   ...   ...    ...    ...    ...    ...    ...    ...   
305  506.0  483.0  0.19  0.20  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
306  490.0  477.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
307  506.0  483.0  0.19  0.20  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
308  505.0  483.0  0.19  0.20  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
309  505.0  483.0  0.19  0.20  0.19  155.0  155.0  155.0  155.0  185.0  185.0   

      X_32   X_33   X_34   X_35   X_36   X_37   X_38  X_39  X_40  X_41  X_42  \
0    185.0  185.0  155.0  155.0  155.0  155.0  0.075   2.0  67.2  68.9  67.5   
1    185.0  185.0  155.0  155.0  155.0  155.0  0.079   2.0  63.7  64.6  64.7   
2    185.0  185.0  155.0  155.0  155.0  155.0  0.079   2.0  63.7  64.6  64.7   
3      NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN   NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN   NaN   
..     ...    ...    ...    ...    ...    ...    ...   ...   ...   ...   ...   
305  185.0  185.0  155.0  155.0  155.0  155.0  0.076   2.0  66.6  67.5  67.2   
306  185.0  185.0  155.0  155.0  155.0  155.0  0.079   2.0  63.1  65.5  64.4   
307  185.0  185.0  155.0  155.0  155.0  155.0  0.075   2.0  66.6  67.5  67.2   
308  185.0  185.0  155.0  155.0  155.0  155.0  0.076   2.0  66.6  67.5  67.2   
309  185.0  185.0  155.0  155.0  155.0  155.0  0.076   2.0  66.6  67.5  67.2   

     X_43  X_44  X_45  X_46  X_47  X_48  X_49  X_50  X_51  X_52  X_53  X_54  \
0    79.8  70.9  80.5  71.2  67.0  76.4  76.0  68.6  79.2  77

In [25]:
TT050304 = test_data[test_data['LINE'] == 'T050304']
TT050307 = test_data[test_data['LINE'] == 'T050307']
TT010305 = test_data[test_data['LINE'] == 'T010305']
TT010306 = test_data[test_data['LINE'] == 'T010306']
TT100304 = test_data[test_data['LINE'] == 'T100304']
TT100306 = test_data[test_data['LINE'] == 'T100306']

TT050304.drop(['LINE'], axis = 1, inplace = True)
TT050307.drop(['LINE'], axis = 1, inplace = True)
TT010305.drop(['LINE'], axis = 1, inplace = True)
TT010306.drop(['LINE'], axis = 1, inplace = True)
TT100304.drop(['LINE'], axis = 1, inplace = True)
TT100306.drop(['LINE'], axis = 1, inplace = True)

In [26]:
TT050304.drop(T050304_col, inplace = True, axis = 1)
TT050307.drop(T050307_col, inplace = True, axis = 1)
TT010305.drop(T010305_col, inplace = True, axis = 1)
TT010306.drop(T010306_col, inplace = True, axis = 1)
TT100304.drop(T100304_col, inplace = True, axis = 1)
TT100306.drop(T100306_col, inplace = True, axis = 1)

In [27]:
TT05 = pd.concat([TT050304, TT050307])
TT01 = pd.concat([TT010305, TT010306])
TT10 = pd.concat([TT100304, TT100306])

TT05.drop(T5drop, inplace = True, axis = 1)
TT01.drop(T0drop, inplace = True, axis = 1)
TT10.drop(T1drop, inplace = True, axis = 1)

TT05 = TT05.fillna(T05.mean())
TT01 = TT01.fillna(T01.mean())
TT10 = TT10.fillna(T10.mean())

TT05 = TT05.fillna(0)
TT01 = TT01.fillna(0)
TT10 = TT10.fillna(0)

In [28]:
TT05.drop(T05_cols, inplace = True, axis = 1)
TT01.drop(T01_cols, inplace = True, axis = 1)
TT10.drop(T10_cols, inplace = True, axis = 1)

In [29]:
TT05_idx = TT05['PRODUCT_CODE'].index
TT05_idx = pd.DataFrame(TT05_idx, columns = ['index'])

TT05c = TT05.columns
TT05scaled = T_05scaler.transform(TT05)
TT05scaled
TT05 = pd.DataFrame(TT05scaled, columns = TT05c)

TT05 = pd.concat([TT05_idx, TT05], axis = 1)
TT05 = TT05.set_index('index')

In [30]:
TT01_idx = TT01['PRODUCT_CODE'].index
TT01_idx = pd.DataFrame(TT01_idx, columns = ['index'])

TT01c = TT01.columns
TT01scaled = T_01scaler.transform(TT01)
TT01 = pd.DataFrame(TT01scaled, columns = TT01c)

TT01 = pd.concat([TT01_idx, TT01], axis = 1)
TT01 = TT01.set_index('index')

In [31]:
TT10_idx = TT10['PRODUCT_CODE'].index
TT10_idx = pd.DataFrame(TT10_idx, columns = ['index'])

TT10c = TT10.columns
TT10scaled = T_10scaler.transform(TT10)
TT10 = pd.DataFrame(TT10scaled, columns = TT10c)

TT10 = pd.concat([TT10_idx, TT10], axis = 1)
TT10 = TT10.set_index('index')

In [32]:
TT05_datas = TT05
TT01_datas = TT01
TT10_datas = TT10

In [33]:
TT05 = TT05.to_numpy()
TT01 = TT01.to_numpy()
TT10 = TT10.to_numpy()

# T05

In [34]:
T05_xtrain, T05_xtest, T05_ytrain, T05_ytest = train_test_split(T05_data, T05_class, test_size = 0.1, random_state = 4)

In [35]:
T05_tab_clf = TabNetClassifier(
    seed = 4,
    momentum = 0.1,
    gamma = 2.0,
    n_steps = 5,
    n_d = 32,
    n_a = 32,
    lambda_sparse = 1e-3,
    optimizer_fn = torch.optim.Adam,
    optimizer_params = dict(lr=1e-2),
    scheduler_params = {
        "step_size" : 10,
        "gamma" : 0.9
    },
    scheduler_fn = torch.optim.lr_scheduler.StepLR,
    mask_type = 'sparsemax',
    verbose = True
)
T05_tab_clf.fit(
    T05_xtrain, T05_ytrain,
    eval_set = [(T05_xtest, T05_ytest)],
    max_epochs = 100, patience = 20,
    batch_size = 128, virtual_batch_size = 32,
    num_workers = 0,
    weights = 1
)
T05_preds = T05_tab_clf.predict(TT05)
T05_preds

Device used : cpu
epoch 0  | loss: 2.0139  | val_0_accuracy: 0.33333 |  0:00:00s
epoch 1  | loss: 1.77854 | val_0_accuracy: 0.25    |  0:00:00s
epoch 2  | loss: 1.81642 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 3  | loss: 1.88079 | val_0_accuracy: 0.58333 |  0:00:00s
epoch 4  | loss: 1.91914 | val_0_accuracy: 0.33333 |  0:00:00s
epoch 5  | loss: 2.17276 | val_0_accuracy: 0.5     |  0:00:00s
epoch 6  | loss: 1.90887 | val_0_accuracy: 0.58333 |  0:00:00s
epoch 7  | loss: 2.00092 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 8  | loss: 1.85529 | val_0_accuracy: 0.41667 |  0:00:01s
epoch 9  | loss: 1.72982 | val_0_accuracy: 0.33333 |  0:00:01s
epoch 10 | loss: 1.73134 | val_0_accuracy: 0.33333 |  0:00:01s
epoch 11 | loss: 1.76981 | val_0_accuracy: 0.5     |  0:00:01s
epoch 12 | loss: 1.70039 | val_0_accuracy: 0.58333 |  0:00:01s
epoch 13 | loss: 1.55129 | val_0_accuracy: 0.25    |  0:00:01s
epoch 14 | loss: 1.90172 | val_0_accuracy: 0.16667 |  0:00:01s
epoch 15 | loss: 1.64606 | val_0_accu

array([1, 0, 0, 0, 2, 0, 0, 0, 0, 1, 0, 0, 2, 0, 1, 0, 1, 2, 1, 1, 0, 0,
       2, 0, 2, 0, 1, 2, 2, 0, 2, 0, 1, 0, 0, 0, 1, 0, 2], dtype=int64)

# T01

In [39]:
T01_xtrain, T01_xtest, T01_ytrain, T01_ytest = train_test_split(T01_data, T01_class, test_size = 0.1, random_state = 4)

In [40]:
T01_tab_clf = TabNetClassifier(
    seed = 4,
    momentum = 0.05,
    gamma = 2.0,
    n_steps = 4,
    n_d = 32,
    n_a = 32,
    lambda_sparse = 1e-4,
    optimizer_fn = torch.optim.Adam,
    optimizer_params = dict(lr=1e-3),
    scheduler_params = {
        "step_size" : 150,
        "gamma" : 0.9
    },
    scheduler_fn = torch.optim.lr_scheduler.StepLR,
    mask_type = 'sparsemax',
    verbose = True
)
T01_tab_clf.fit(
    T01_xtrain, T01_ytrain,
    eval_set = [(T01_xtest, T01_ytest)],
    max_epochs = 100, patience = 20,
    batch_size = 1024, virtual_batch_size = 64,
    num_workers = 0,
    weights = 1
)
T01_preds = T01_tab_clf.predict(TT01)
T01_preds

Device used : cpu
epoch 0  | loss: 1.42579 | val_0_accuracy: 0.23077 |  0:00:00s
epoch 1  | loss: 1.52781 | val_0_accuracy: 0.38462 |  0:00:00s
epoch 2  | loss: 1.86405 | val_0_accuracy: 0.38462 |  0:00:00s
epoch 3  | loss: 1.54529 | val_0_accuracy: 0.38462 |  0:00:00s
epoch 4  | loss: 1.59056 | val_0_accuracy: 0.61538 |  0:00:00s
epoch 5  | loss: 1.63914 | val_0_accuracy: 0.38462 |  0:00:00s
epoch 6  | loss: 1.60751 | val_0_accuracy: 0.46154 |  0:00:00s
epoch 7  | loss: 1.29221 | val_0_accuracy: 0.46154 |  0:00:00s
epoch 8  | loss: 1.68078 | val_0_accuracy: 0.69231 |  0:00:00s
epoch 9  | loss: 1.3425  | val_0_accuracy: 0.61538 |  0:00:00s
epoch 10 | loss: 1.5948  | val_0_accuracy: 0.46154 |  0:00:00s
epoch 11 | loss: 1.22785 | val_0_accuracy: 0.53846 |  0:00:00s
epoch 12 | loss: 1.54243 | val_0_accuracy: 0.46154 |  0:00:00s
epoch 13 | loss: 1.74254 | val_0_accuracy: 0.46154 |  0:00:00s
epoch 14 | loss: 1.41968 | val_0_accuracy: 0.38462 |  0:00:00s
epoch 15 | loss: 1.62162 | val_0_accu

array([1, 0, 0, 2, 1, 1, 1, 1, 0, 2, 2, 1, 0, 0, 1, 0, 2, 0, 2, 1, 1, 2,
       1, 1, 0, 1, 0, 1], dtype=int64)

# T10

In [42]:
T10_xtrain, T10_xtest, T10_ytrain, T10_ytest = train_test_split(T10_data, T10_class, test_size = 0.1, random_state = 4)

In [43]:
T10_tab_clf = TabNetClassifier(
    seed = 4,
    momentum = 0.1,
    gamma = 1.5,
    n_steps = 3,
    n_d = 32,
    n_a = 32,
    lambda_sparse = 1e-3,
    optimizer_fn = torch.optim.Adam,
    optimizer_params = dict(lr=1e-2),
    scheduler_params = {
        "step_size" : 100,
        "gamma" : 0.5
    },
    scheduler_fn = torch.optim.lr_scheduler.StepLR,
    mask_type = 'sparsemax',
    verbose = True
)
T10_tab_clf.fit(
    T10_xtrain, T10_ytrain,
    eval_set = [(T10_xtest, T10_ytest)],
    max_epochs = 100, patience = 20,
    batch_size = 512, virtual_batch_size = 64,
    num_workers = 0,
    weights = 1
)
T10_preds = T10_tab_clf.predict(TT10)
T10_preds

Device used : cpu
epoch 0  | loss: 1.60371 | val_0_accuracy: 0.28571 |  0:00:00s
epoch 1  | loss: 1.45861 | val_0_accuracy: 0.57143 |  0:00:00s
epoch 2  | loss: 1.38604 | val_0_accuracy: 0.62857 |  0:00:00s
epoch 3  | loss: 1.38069 | val_0_accuracy: 0.77143 |  0:00:00s
epoch 4  | loss: 1.27991 | val_0_accuracy: 0.6     |  0:00:00s
epoch 5  | loss: 1.29914 | val_0_accuracy: 0.65714 |  0:00:00s
epoch 6  | loss: 1.36191 | val_0_accuracy: 0.57143 |  0:00:00s
epoch 7  | loss: 1.31879 | val_0_accuracy: 0.51429 |  0:00:00s
epoch 8  | loss: 1.20076 | val_0_accuracy: 0.48571 |  0:00:00s
epoch 9  | loss: 1.14761 | val_0_accuracy: 0.48571 |  0:00:00s
epoch 10 | loss: 1.07721 | val_0_accuracy: 0.48571 |  0:00:00s
epoch 11 | loss: 0.96141 | val_0_accuracy: 0.4     |  0:00:00s
epoch 12 | loss: 0.99769 | val_0_accuracy: 0.4     |  0:00:00s
epoch 13 | loss: 0.95317 | val_0_accuracy: 0.25714 |  0:00:00s
epoch 14 | loss: 1.01849 | val_0_accuracy: 0.34286 |  0:00:01s
epoch 15 | loss: 1.00167 | val_0_accu

array([1, 0, 2, 1, 1, 1, 1, 1, 0, 2, 1, 0, 1, 1, 0, 2, 1, 2, 0, 0, 1, 1,
       0, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1, 1, 2, 0, 1, 1, 2, 1, 1, 1, 1,
       1, 2, 0, 2, 2, 1, 0, 2, 2, 1, 2, 1, 1, 1, 1, 1, 2, 1, 0, 1, 2, 1,
       1, 1, 1, 1, 0, 1, 0, 0, 1, 1, 1, 1, 2, 1, 2, 0, 1, 1, 1, 2, 1, 1,
       2, 1, 1, 2, 2, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 1, 1, 1, 2, 2, 1, 1,
       2, 1, 2, 1, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 1, 2, 1, 1, 2, 1, 1, 1,
       1, 1, 1, 0, 0, 1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 0, 1, 1, 2, 1, 1, 2,
       1, 2, 1, 2, 2, 0, 1, 1, 1, 1, 1, 2, 1, 2, 1, 1, 2, 2, 1, 1, 1, 1,
       1, 2, 1, 1, 1, 0, 2, 2, 1, 1, 1, 2, 1, 2, 1, 1, 1, 2, 1, 0, 2, 1,
       2, 2, 1, 1, 1, 2, 1, 1, 1, 1, 2, 0, 1, 1, 1, 1, 0, 2, 1, 1, 0, 1,
       2, 1, 1, 1, 2, 1, 1, 1, 1, 2, 1, 1, 1, 1, 0, 1, 2, 1, 1, 1, 1, 0,
       1], dtype=int64)

In [44]:
TT05_predictions = pd.DataFrame(T05_preds, columns = ['prediction_label'])
TT01_predictions = pd.DataFrame(T01_preds, columns = ['prediction_label'])
TT10_predictions = pd.DataFrame(T10_preds, columns = ['prediction_label'])

In [45]:
TT05_idxf = TT05_datas.index
TT05_p = pd.DataFrame(TT05_idxf, columns = ['index'])
TT05_predictions = pd.concat([TT05_p, TT05_predictions], axis = 1)
TT05_predictions = TT05_predictions.set_index('index')

TT01_idxf = TT01_datas.index
TT01_p = pd.DataFrame(TT01_idxf, columns = ['index'])
TT01_predictions = pd.concat([TT01_p, TT01_predictions], axis = 1)
TT01_predictions = TT01_predictions.set_index('index')

TT10_idxf = TT10_datas.index
TT10_p = pd.DataFrame(TT10_idxf, columns = ['index'])
TT10_predictions = pd.concat([TT10_p, TT10_predictions], axis = 1)
TT10_predictions = TT10_predictions.set_index('index')

In [46]:
final_test = pd.concat([TT05_predictions, TT01_predictions, TT10_predictions])
final_test

prediction_label
index                  
7                     1
8                     0
14                    0
35                    0
41                    2
...                 ...
301                   1
305                   1
307                   1
308                   0
309                   1

[310 rows x 1 columns]

In [47]:
final_test = final_test.sort_index(ascending=True)
final_test['prediction_label']

index
0      1
1      1
2      0
3      1
4      1
      ..
305    1
306    2
307    1
308    0
309    1
Name: prediction_label, Length: 310, dtype: int64

In [48]:
#52
sample_submission = pd.read_csv('sample_submission.csv')
sample_submission['Y_Class'] = final_test['prediction_label']
display(sample_submission.head())
sample_submission.to_csv('line3_otherdrop_std0drop_robust_Tabnetclass_fill0_submission.csv',index=False)

PRODUCT_ID  Y_Class
0   TEST_000        1
1   TEST_001        1
2   TEST_002        0
3   TEST_003        1
4   TEST_004        1

In [49]:
final_test['prediction_label'].value_counts()

1    178
2     70
0     62
Name: prediction_label, dtype: int64

In [50]:
np.array(final_test['prediction_label'])

array([1, 1, 0, 1, 1, 0, 0, 1, 0, 2, 0, 2, 0, 0, 0, 2, 2, 1, 1, 1, 1, 0,
       1, 1, 1, 0, 0, 2, 1, 1, 0, 1, 1, 1, 0, 0, 1, 2, 1, 1, 1, 2, 0, 1,
       1, 1, 1, 1, 2, 0, 1, 2, 0, 0, 0, 1, 1, 2, 2, 0, 0, 1, 0, 1, 0, 0,
       2, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 2, 1, 1, 0, 1, 1, 1, 1, 1,
       0, 2, 1, 0, 0, 1, 0, 1, 1, 1, 1, 2, 2, 0, 1, 1, 1, 1, 1, 1, 2, 1,
       1, 2, 1, 1, 0, 1, 2, 1, 0, 1, 1, 1, 1, 1, 2, 1, 1, 1, 0, 1, 2, 1,
       1, 2, 2, 0, 1, 2, 2, 2, 1, 0, 0, 2, 1, 0, 2, 2, 0, 1, 1, 2, 1, 1,
       1, 1, 2, 2, 1, 1, 2, 1, 1, 1, 1, 2, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1,
       0, 1, 2, 2, 1, 1, 1, 1, 1, 0, 2, 1, 2, 1, 1, 1, 1, 0, 1, 1, 0, 2,
       0, 1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 2, 1, 2, 0, 0, 2, 1, 1, 2, 1,
       2, 1, 2, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 2, 0, 1, 1, 1, 1, 2,
       1, 2, 1, 1, 1, 0, 0, 0, 2, 0, 2, 0, 1, 2, 1, 2, 1, 1, 2, 1, 0, 0,
       1, 1, 2, 1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1, 2, 0, 1, 0, 0, 0,
       1, 2, 1, 1, 0, 1, 0, 2, 2, 2, 1, 1, 1, 1, 2,